In [1]:
import numpy as np
import keras.backend as K
import keras
import pandas as pd

Using TensorFlow backend.


In [2]:
from keras.models import load_model

In [3]:
from keras.models import Sequential
from keras.layers import Dense, Dropout, Flatten, Activation
from keras.layers import Conv2D, MaxPooling2D, BatchNormalization

In [7]:
import cv2

In [4]:
def Model():
    INPUT_SHAPE = (64, 64, 3)
    num_classes = 2
    model = Sequential()
    model.add(Conv2D(32, (3, 3), padding='same',
                     input_shape=INPUT_SHAPE))
    model.add(Activation('relu'))
    model.add(Conv2D(32, (3, 3)))
    model.add(Activation('relu'))
    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(Dropout(0.25))

    model.add(Conv2D(64, (3, 3), padding='same'))
    model.add(Activation('relu'))
    model.add(Conv2D(64, (3, 3)))
    model.add(Activation('relu'))
    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(Dropout(0.25))

    model.add(Flatten())
    model.add(Dense(512))
    model.add(Activation('relu'))
    model.add(Dropout(0.5))
    model.add(Dense(num_classes))
    model.add(Activation('softmax'))

#     opt = keras.optimizers.RMSprop(lr=0.0001, decay=1e-6)
#     # Let's train the model using RMSprop
#     model.compile(loss='binary_crossentropy',
#                   optimizer=opt,
#                   metrics=['accuracy'])
    return model

In [5]:
model = Model()
model.load_weights('./smiledetection.h5')

In [32]:
!pip install opencv-python

In [8]:
# TEXT SPECIFICATIONs
font                   = cv2.FONT_HERSHEY_SIMPLEX
bottomLeftCornerOfText = (50,50)
fontScale              = 1
fontColor              = (0,0,255)
lineType               = 2

In [9]:
def detectSmileAndOutput(matimage, param):
      image = matimage
      colored_im = np.copy(image)

      image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

      face_cascade = cv2.CascadeClassifier(cv2.data.haarcascades+'haarcascade_frontalface_default.xml')
      # FACE DETECTION
      # if necessary, modify these parameters until you successfully identify every face in a given image
      faces = face_cascade.detectMultiScale(image, param, 2)

      padding_w = 10
      padding_h = 10

      # Choosing the person with larger image area: so as to detect smile on only one person
      max_w = 0
      max_h = 0
      max_x = 0
      max_y = 0
      for (x, y, w, h) in faces:
        if(w*h>max_w*max_h):
          max_w = w
          max_h = h
          max_x = x
          max_y = y

      # BOUNDING BOX COORDINATES
      x, y, w, h = max_x, max_y, max_w, max_h

      roi = colored_im[y-padding_h:y+h+padding_h, x-padding_w:x+w+padding_w]
#       image_gray = cv2.cvtColor(roi, cv2.COLOR_RGB2GRAY)
      # NOW image_grey IS THE CROPPED IMAGE OF SINGLE HUMAN 8IN GRAYSCALE

      # PRE-PROCESSING INPUT IMAGE
#       image_gray = cv2.cvtColor(roi, cv2.COLOR_RGB2GRAY)
      image_gray=  roi/255.0
      img = cv2.resize(image_gray, (64, 64))
      temp = np.zeros(shape = (64, 64, 3))
#       for i in range(3):
#         temp[:,:,i] = img

      temp = temp.reshape(1, 64, 64, 3)

      # PREDICTING USING TRAINED MODEL
      proba = model.predict(temp)

      print(proba)

      # ASSIGNING CLASS AND TEXT-ON-IMAGE
      isSmiling = proba[0][0]>proba[0][1]
      if isSmiling:
        textOnImage = 'Smiling: ' + str('%.2f' % proba[0][0])
      else:
        textOnImage = 'Not Smiling: ' + str('%.2f' % proba[0][1])

      # PUTTING TEXT ON IMAGE
      cv2.putText(colored_im,textOnImage, 
          bottomLeftCornerOfText, 
          font, 
          fontScale,
          fontColor,
          lineType)

      # PUTTING BOUNDING BOX ON IMAGE: BOX PREVIOUSLY CALCULATED USING CASCADE
      cv2.rectangle(colored_im,(x,y),(x+w,y+h),(255,0,0),3)

      # IMSHOW FINAL IMAGE WITH FACE AND SMILE DETECTION
      cv2.imshow('smile', colored_im)

In [10]:
vid = cv2.VideoCapture(0) 
  
while(True): 
      
    # Capture the video frame 
    # by frame 
    ret, frame = vid.read() 
  
    # Display the resulting frame 
#     cv2.imshow('frame', frame)
    detectSmileAndOutput(frame, 1.2)
    # the 'q' button is set as the 
    # quitting button you may use any 
    # desired button of your choice 
    if cv2.waitKey(1) & 0xFF == ord('q'): 
        break
  
# After the loop release the cap object 
vid.release() 
# Destroy all the windows 
cv2.destroyAllWindows() 

[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]
[[0.251433 0.748567]]


error: OpenCV(4.2.0) C:\projects\opencv-python\opencv\modules\imgproc\src\resize.cpp:4045: error: (-215:Assertion failed) !ssize.empty() in function 'cv::resize'


Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callb

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callb

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callb

...

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callb

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callb

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callb

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callb

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\Karan\Anaconda3\lib\asyncio\events.py", line 145, in _run
    self._callback(*self._args)
  File "C:\Users\Karan\Anaconda3\lib\asyncio\selector_events.py", line 141, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callb